In [1]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import re
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
import string
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from keras.models import Model
from keras.layers import LSTM, Activation, Dense, Dropout, Input, Embedding, SpatialDropout1D
from keras.optimizers import RMSprop
from tensorflow.keras.preprocessing.text import Tokenizer
from keras.utils import to_categorical
from keras.callbacks import EarlyStopping, ModelCheckpoint
from keras.models import Sequential
from keras.utils import pad_sequences
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.metrics import confusion_matrix
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', 255)

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [2]:
!nvidia-smi

/bin/bash: line 1: nvidia-smi: command not found


In [3]:
import numpy as np
import pandas as pd


In [4]:

url = "https://ai.stanford.edu/~amaas/data/sentiment/aclImdb_v1.tar.gz"
!wget {url}

archive_name = url.split('/')[-1]
!tar -xf {archive_name}

print(f"IMDB dataset downloaded and extracted from {archive_name}")

dataset_dir = './aclImdb'


print("\nDataset directory structure:")
!ls -R {dataset_dir}

Streaming output truncated to the last 5000 lines.
12999_0.txt  20500_0.txt  2800_0.txt   3550_0.txt   43001_0.txt  5502_0.txt
13000_0.txt  2050_0.txt   28001_0.txt  35501_0.txt  43002_0.txt  5503_0.txt
1300_0.txt   20501_0.txt  28002_0.txt  35502_0.txt  43003_0.txt  5504_0.txt
13001_0.txt  20502_0.txt  28003_0.txt  35503_0.txt  43004_0.txt  5505_0.txt
13002_0.txt  20503_0.txt  28004_0.txt  35504_0.txt  43005_0.txt  5506_0.txt
13003_0.txt  20504_0.txt  28005_0.txt  35505_0.txt  43006_0.txt  5507_0.txt
13004_0.txt  20505_0.txt  28006_0.txt  35506_0.txt  43007_0.txt  5508_0.txt
13005_0.txt  20506_0.txt  28007_0.txt  35507_0.txt  43008_0.txt  5509_0.txt
13006_0.txt  20507_0.txt  28008_0.txt  35508_0.txt  43009_0.txt  55_0.txt
13007_0.txt  20508_0.txt  28009_0.txt  35509_0.txt  430_0.txt	 5510_0.txt
13008_0.txt  20509_0.txt  280_0.txt    355_0.txt    43010_0.txt  551_0.txt
13009_0.txt  205_0.txt	  28010_0.txt  35510_0.txt  4301_0.txt	 5511_0.txt
130_0.txt    20510_0.txt  2801_0.txt   3551_

In [5]:
import pandas as pd
import os

def load_imdb_data(path):
    data = {'text': [], 'sentiment': []}
    for sentiment_type in ['neg', 'pos']:
        sentiment_path = os.path.join(path, sentiment_type)

        if not os.path.exists(sentiment_path):
            print(f"Warning: Directory not found: {sentiment_path}")
            continue
        for filename in os.listdir(sentiment_path):

            if filename.endswith('.txt'):
                with open(os.path.join(sentiment_path, filename), 'r', encoding='utf-8') as f:
                    data['text'].append(f.read())
                    data['sentiment'].append(1 if sentiment_type == 'pos' else 0)
    return pd.DataFrame(data)

dataset_dir = './aclImdb'


train_path = os.path.join(dataset_dir, 'train')
train_df = load_imdb_data(train_path)
print(f"\nTraining data loaded, shape: {train_df.shape}")
display(train_df.head())


test_path = os.path.join(dataset_dir, 'test')
test_df = load_imdb_data(test_path)
print(f"\nTest data loaded, shape: {test_df.shape}")
display(test_df.head())


Training data loaded, shape: (25000, 2)


text  \
0  Making the film as dark and visually fuzzy as possible in order to cover up the budget deficiencies is an often-used strategy in low-budget horror films, but this one takes it too far. It is SO poorly lit and murky (and it takes place almost entirely ...   
1  A trio of low-life criminals, led by Matt Dillon, botches a late-night burglary. They flee but quickly cross paths with the police who just happen to be in hot pursuit of a terrorist. Of course the police mistake the burglar gang for the terrorist, th...   
2  There is a reason why certain films go straight to video and of course the obvious reason is that if its too naughty for theater audience then release straight to video. Of course it really wouldn't be fair to the films that are good and yet they are ...   
3  Would someone tell shaq to stick to what he is good at basketball. This movie was not even entertaining on a stupid level. In this movie shaq plays a genie who lives in a boom box is that not orginal a genie in a boom box instead of a lamp. He is supp...   
4  The past creeps up on a rehab-addict when he reconnects with his ill brother and a former girlfriend after what he hopes was his last stint in detox. "Life's dramas", presented here in the most simplistic way imaginable (not even the writing has any b...   

   sentiment  
0          0  
1          0  
2          0  
3          0  
4          0


Test data loaded, shape: (25000, 2)


text  \
0  1st watched 4/30/2009 - 4 out of 10 (Dir-John Waters): Corny Waters-like comedy musical with some funny scenes and good parts but it didn't make a whole worthwhile experience. John Waters directed this music-filled spoof of the fifties scene with John...   
1  ***SPOILERS*** ***SPOILERS*** HERE ON EARTH / (2000) 1/2* (out of four)<br /><br />Mark Piznarski's "Here on Earth" holds the record for a movie containing the most recycled material in 96 minutes. Literally every contrivance, cliché, and familiar plo...   
2  I give this piece of Hollywood trash 1 out 10! Seriously! I mean, I like comedy as much as the next guy. I also can take just plain stupid comedy and actually sit back and laugh with it. But this film had nothing to laugh at OR with.<br /><br />I like...   
3  I have seen both the MST3K version and the uncut version. I rather enjoyed it. Either way, it wasn't that bad of a movie. Sure it moved a bit slow at times. I liked it.<br /><br />As far as MST3K goes, they only did the movies they could get the right...   
4  I've been on a bad run of films. This is a clinker about an arson plot and a psychopath. Tom Skerrit, whom I really enjoy, was pretty young here. He is a builder with a passion, but he has a partner whose profit motive includes over-insuring and burni...   

   sentiment  
0          0  
1          0  
2          0  
3          0  
4          0

In [6]:
train_df['text'][7]

"It's the early 80s. There's a group of suspiciously old-looking teens. And there's a maniac stalking around. Yes, this is slasherville.<br /><br />This movie is called Pranks. Why is it called Pranks? I haven't the faintest idea. Unless your idea of a great prank is to repeatedly hit someone's dinner with a baseball bat - on balance, not a great prank; in fact quite a rubbish prank if truth be told. But there you go.<br /><br />The film itself concerns a group of teenagers who are tasked with cleaning out a decommissioned dormitory. They become aware that a psychopath is on the loose. To combat this development, they split up and wander about in the dark. It ends in tears for most of them.<br /><br />Pranks is a badly made slasher movie. The DVD release I viewed was the Vipco one. It appears to be cut of a fair bit of violence. This makes the DVD even more pointless because, let's face it, a slasher movie shorn of violence is a waste of time. For slasher-film and video nasty completis

In [7]:
train_df['sentiment'].value_counts()

sentiment
0    12500
1    12500
Name: count, dtype: int64

In [8]:
train_df.isnull().sum()

text         0
sentiment    0
dtype: int64

In [9]:
train_df.duplicated().sum()

np.int64(96)

In [10]:
train_df.drop_duplicates(inplace=True)


# best preprocessing

In [11]:
import re
def remove_tags(raw_text):
  cleaned_text=re.sub(re.compile('<.*?>'), '.', raw_text)
  return cleaned_text

In [12]:
train_df['text']=train_df['text'].apply(remove_tags)

In [13]:
from nltk.corpus import stopwords
import nltk

nltk.download('stopwords')
sw_list=stopwords.words('english')

train_df['text']=train_df['text'].apply(lambda x: " ".join([item for item in x.split() if item not in sw_list]))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [14]:


X = train_df.iloc[:,0:1]
y =train_df['sentiment']

In [15]:
X.head()

text
0  Making film dark visually fuzzy possible order cover budget deficiencies often-used strategy low-budget horror films, one takes far. It SO poorly lit murky (and takes place almost entirely night, boot) often end virtually looking black screen (althoug...
1  A trio low-life criminals, led Matt Dillon, botches late-night burglary. They flee quickly cross paths police happen hot pursuit terrorist. Of course police mistake burglar gang terrorist, real terrorist gets away, burglars forced take refuge small di...
2  There reason certain films go straight video course obvious reason naughty theater audience release straight video. Of course really fair films good yet also released straight video. This one exception although film good actors least actors potential:...
3  Would someone tell shaq stick good basketball. This movie even entertaining stupid level. In movie shaq plays genie lives boom box orginal genie boom box instead lamp. He supposed help little boy played equally annoying francais cappra. This movie fli...
4  The past creeps rehab-addict reconnects ill brother former girlfriend hopes last stint detox. "Life's dramas", presented simplistic way imaginable (not even writing bite wit). The cast made attractive looking actors smiling glumly one another, music p...

In [16]:
y

0        0
1        0
2        0
3        0
4        0
5        0
6        0
7        0
8        0
9        0
10       0
11       0
12       0
13       0
14       0
15       0
16       0
17       0
18       0
19       0
20       0
21       0
22       0
23       0
24       0
25       0
26       0
27       0
28       0
29       0
30       0
31       0
32       0
33       0
34       0
35       0
36       0
37       0
38       0
39       0
40       0
41       0
42       0
43       0
44       0
45       0
46       0
47       0
48       0
49       0
50       0
51       0
52       0
53       0
54       0
55       0
56       0
57       0
58       0
59       0
60       0
61       0
62       0
63       0
64       0
65       0
66       0
67       0
68       0
69       0
70       0
71       0
72       0
73       0
74       0
75       0
76       0
77       0
78       0
79       0
80       0
81       0
82       0
83       0
84       0
85       0
86       0
87       0
88       0
89       0
90       0
91       0
92       0
93       0
94       0
95       0
96       0
97       0
98       0
99       0
100      0
101      0
102      0
103      0
104      0
105      0
106      0
107      0
108      0
109      0
110      0
111      0
112      0
113      0
114      0
115      0
116      0
117      0
118      0
119      0
120      0
121      0
122      0
123      0
124      0
125      0
126      0
127      0
128      0
129      0
130      0
131      0
132      0
133      0
134      0
135      0
136      0
137      0
138      0
139      0
140      0
141      0
142      0
143      0
144      0
145      0
146      0
147      0
148      0
149      0
150      0
151      0
152      0
153      0
154      0
155      0
156      0
157      0
158      0
159      0
160      0
161      0
162      0
163      0
164      0
165      0
166      0
167      0
168      0
169      0
170      0
171      0
172      0
173      0
174      0
175      0
176      0
177      0
178      0
179      0
180      0
181      0
182      0
183      0
184      0
185      0
186      0
187      0
188      0
189      0
190      0
191      0
192      0
193      0
194      0
195      0
196      0
197      0
198      0
199      0
200      0
201      0
202      0
203      0
204      0
205      0
206      0
207      0
208      0
209      0
210      0
211      0
212      0
213      0
214      0
215      0
216      0
217      0
218      0
219      0
220      0
221      0
222      0
223      0
224      0
225      0
226      0
227      0
228      0
229      0
230      0
231      0
232      0
233      0
234      0
235      0
236      0
237      0
238      0
239      0
240      0
241      0
242      0
243      0
244      0
245      0
246      0
247      0
248      0
249      0
250      0
251      0
252      0
253      0
254      0
255      0
256      0
257      0
258      0
259      0
260      0
261      0
262      0
263      0
264      0
265      0
266      0
267      0
268      0
269      0
270      0
271      0
272      0
273      0
274      0
275      0
276      0
277      0
278      0
279      0
280      0
281      0
282      0
283      0
284      0
285      0
286      0
287      0
288      0
289      0
290      0
291      0
292      0
293      0
294      0
295      0
296      0
297      0
298      0
299      0
300      0
301      0
302      0
303      0
304      0
305      0
306      0
307      0
308      0
309      0
310      0
311      0
312      0
313      0
314      0
315      0
316      0
317      0
318      0
319      0
320      0
321      0
322      0
323      0
324      0
325      0
326      0
327      0
328      0
329      0
330      0
331      0
332      0
333      0
334      0
335      0
336      0
337      0
338      0
339      0
340      0
341      0
342      0
343      0
344      0
345      0
346      0
347      0
348      0
349      0
350      0
351      0
352      0
353      0
354      0
355      0
356      0
357      0
358      0
359      0
360      0
361      0
362      0
363    

In [17]:
from sklearn.preprocessing import LabelEncoder
encoder=LabelEncoder()

y=encoder.fit_transform(y)

In [18]:

# Applying BoW
from sklearn.feature_extraction.text import CountVectorizer
cv = CountVectorizer()

In [ ]:
from sklearn.naive_bayes import GaussianNB
gnb = GaussianNB()


X_bow = cv.fit_transform(X['text']).toarray()


from sklearn.model_selection import train_test_split
X_train_bow, X_test_bow, y_train, y_test = train_test_split(X_bow, y, test_size=0.2, random_state=42)

gnb.fit(X_train_bow, y_train)

In [ ]:
y_pred=gnb.predict(X_test_bow)
from sklearn.metrics import accuracy_score , confusion_matrix
accuracy_score(y_test , y_pred)

In [ ]:
confusion_metrics(y_test , y_ pred)

In [ ]:
from sklearn.ensemble import RandomForestClassifier
rf = RandomForestClassifier()

rf.fit(X_train_bow,y_train)

y_pred = rf.predict(X_test_bow)

accuracy_score(y_test,y_pred)



In [ ]:
cv= CounterVectorizer(max_features=3000)

X_train_bow=cv.fit_transform(X_train['review']).toarray()
X_test_bow=cv.fit_transform(X_test['review']).toarray()

rf=RandomForrestClassifier()
rf.fit(X_train_bow , y_train)
y_pred=rf.predict(X_test_bow)
accuracy_score(y_test , y_pred)


## N-grams

In [ ]:

cv = CountVectorizer(ngram_range=(1,2),max_features=5000)

X_train_bow = cv.fit_transform(X_train['review']).toarray()
X_test_bow = cv.transform(X_test['review']).toarray()

rf = RandomForestClassifier()

rf.fit(X_train_bow,y_train)
y_pred = rf.predict(X_test_bow)
accuracy_score(y_test,y_pred)

#tfidf

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
tfidf=TfidfVectorizer()

In [ ]:

X_train_tfidf = tfidf.fit_transform(X_train['review']).toarray()
X_test_tfidf = tfidf.transform(X_test['review'])

In [ ]:
rf = RandomForestClassifier()

rf.fit(X_train_tfidf,y_train)
y_pred = rf.predict(X_test_tfidf)

accuracy_score(y_test,y_pred)